
# Standardized only all inputs and output


The purpose of this is to bring features and outputs to the same scale.  

Run this model on the web at: 



## Standardization

$  \large x_{stand} = \frac {(x - \mu _x)}{\sigma _x}   $




## Experiment description

This run is done using CFD. Used an 80% train test split. 
The CFD data has 56 samples where each sample has 27 features. There are 10 inputs and 17 outputs. All inputs and outputs were used. 

 


Train_X.........(44, 10)

Train_y.........(44, 17)

Test_X.........(12, 10)

Test_y.........(12, 17)





In [1]:
######################################################
##
## regression with scaling and DL for system control
##
######################################################

import torch
import numpy as np
import pandas as pd
import sklearn
import torch.nn as nn
import torch.nn.functional as F

from torch.utils.data import TensorDataset, DataLoader
from sklearn.model_selection import train_test_split
## coefficient of determination (R**2)
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler

#######################################################

N_EPOCHS = 10000
batch_size = 5
learning_rate = 0.001    ## 0.01  ## 0.1 ## 1e-5 

#######################################################

np.set_printoptions(suppress=True)
torch.set_printoptions(sci_mode=False)


In [2]:

CFD_raw_data = pd.read_csv('CFD.6.2022.csv') 


In [3]:

headers_list = CFD_raw_data.columns.values.tolist()
## print(headers_list)
## print(len(headers_list))
## print(headers_list[27])

for i, name in enumerate(headers_list):
    print((i, name))
    

(0, 'index')
(1, 'i_pul_coal_inj_kg_thm')
(2, 'i_nat_gas_inj_kg_thm')
(3, 'i_nat_gas_t_k')
(4, 'i_o2_vol_perce')
(5, 'i_bf_windrate_nm3_hr')
(6, 'i_hb_moist_g_nm3')
(7, 'i_hot_blast_press_pa')
(8, 'i_hot_blast_temp_k')
(9, 'i_coke_weight_kg')
(10, 'i_ore_weight_kg')
(11, 'o_tuyere_exit_velo_m_s')
(12, 'o_tuyere_t_k')
(13, 'o_raceway_flame_temp_k')
(14, 'o_raceway_coal_burn_perce')
(15, 'o_raceway_volume_m')
(16, 'o_raceway_depth _m')
(17, 'o_shaft_co_utiliz')
(18, 'o_shaft_h2_utiliz')
(19, 'o_shaft_top_gas_temp_c')
(20, 'o_shaft_press_drop_pa')
(21, 'o_shaft_coke_rate_kg_thm')
(22, 'o_shaft_cohesive_zone_tip_height_m')
(23, 'o_shaft_cohes_zone_root_height_m')
(24, 'o_shaft_co_v_perc')
(25, 'o_shaft_co2_v_perc')
(26, 'o_shaft_h2_v_perce')
(27, 'o_shaft_n2_v_perc')


In [4]:

CFDdata_np = CFD_raw_data.to_numpy()

## print(CFDdata_np)
print(CFDdata_np.shape)


(56, 28)


In [5]:

#######################################################

input_indeces  = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
output_indeces = [11, 12 ,13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27]

#######################################################

X = CFDdata_np[:, input_indeces]

y = CFDdata_np[:, output_indeces]

print(X.shape)
print(y.shape)

#######################################################

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=42)

#######################################################

print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)



(56, 10)
(56, 17)
(44, 10)
(12, 10)
(44, 17)
(12, 17)


In [6]:

## fix data type
X_train  = X_train.astype(np.float32)
X_test   = X_test.astype(np.float32)
y_train  = y_train.astype(np.float32)
y_test   = y_test.astype(np.float32)



##################################################



ss_X = StandardScaler()
obj_X = ss_X.fit(X_train)
X_train_scaled = obj_X.transform(X_train)
X_test_scaled  = obj_X.transform(X_test)

ss_y = StandardScaler()
obj_y = ss_y.fit(y_train)
y_train_scaled = obj_y.transform(y_train)
y_test_scaled  = obj_y.transform(y_test)



##################################################



In [7]:

X_train_tr  = torch.from_numpy(X_train_scaled)
X_test_tr   = torch.from_numpy(X_test_scaled)
y_train_tr  = torch.from_numpy(y_train_scaled)
y_test_tr   = torch.from_numpy(y_test_scaled)


In [8]:



print(X_train_tr.shape)
print(X_test_tr.shape)
print(y_train_tr.shape)
print(y_test_tr.shape)





torch.Size([44, 10])
torch.Size([12, 10])
torch.Size([44, 17])
torch.Size([12, 17])


In [9]:

#######################################################
## define dataset

train_ds = TensorDataset(X_train_tr, y_train_tr)

#######################################################
## define dataloader

train_dl = DataLoader(train_ds, batch_size, shuffle=True)


#######################################################


## Deep Learning Architecture

All inputs and outputs are scaled. 

In [10]:
    
#############################################################


class DL_Net_Dropout(nn.Module):
    
    ## initialize the layers
    def __init__(self):
        super().__init__()
        
        
        self.linear1 = nn.Linear(10, 32)
        self.act1    = nn.Tanh() 
        self.linear2 = nn.Linear(32, 24)
        self.act2    = nn.Tanh() 
        self.linear3 = nn.Linear(24, 17)
        self.dropout = nn.Dropout(0.25)
    
    ## perform inference
    def forward(self, x):
        
        x = self.linear1(x)
        x = self.act1(x)
        x = self.dropout(x)
        x = self.linear2(x)
        x = self.act2(x)
        x = self.dropout(x)
        x = self.linear3(x)
       
        return x

      
#############################################################


In [14]:

#######################################################


def fit(num_epochs, model, loss_fn, opt):
    
    for epoch in range(num_epochs):
        for xb, yb in train_dl:
            pred = model(xb)
            loss = loss_fn(pred, yb)
            loss.backward()
            opt.step()
            opt.zero_grad()
            print('Training loss:', loss_fn(pred, yb))
            
    pred = model(X_train_tr)        
    print('Training loss:', loss_fn(  pred,                   y_train_tr         ))
    print('Training R**2:', r2_score( pred.detach().numpy(),  y_train_tr.numpy()  ))
    

#######################################################


In [15]:

model = DL_Net_Dropout()
opt = torch.optim.Adam(   model.parameters(), lr=learning_rate   )
loss_fn = F.mse_loss

## loss_fn = F.l1_loss



In [16]:

fit(N_EPOCHS, model, loss_fn, opt)


Training loss: tensor(1.7200, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.7614, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.6749, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.7186, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.9713, grad_fn=<MseLossBackward0>)
Training loss: tensor(1.1534, grad_fn=<MseLossBackward0>)
Training loss: tensor(1.0725, grad_fn=<MseLossBackward0>)
Training loss: tensor(1.1733, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.4930, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.7367, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.6270, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.8969, grad_fn=<MseLossBackward0>)
Training loss: tensor(1.4659, grad_fn=<MseLossBackward0>)
Training loss: tensor(1.5956, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.8597, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.5763, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.8163, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.1499, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3918, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1640, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3196, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1675, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.5928, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2025, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2675, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1667, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2628, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2111, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2427, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2806, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3206, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2119, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3919, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3634, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.1455, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2538, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2264, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2395, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3841, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1968, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2515, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2522, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1933, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2044, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2694, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1847, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.4786, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1775, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.5093, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1766, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1182, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.1416, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3007, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2892, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2086, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0957, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2175, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1735, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2900, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1694, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3442, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1763, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1514, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1787, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1458, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2901, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3315, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2113, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.1064, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1452, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2083, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2643, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1273, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3944, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1551, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.3775, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1298, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1591, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2234, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1927, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1309, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.4163, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1103, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1182, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2481, grad_fn=<MseLossBackward0>)
Training loss:

...

Training loss: tensor(0.1407, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1566, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0922, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1125, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1358, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1097, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1619, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1482, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1112, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1622, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1188, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1779, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0971, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1544, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1465, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0935, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1937, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.1402, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1257, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1018, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1007, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0846, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0788, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1435, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1146, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0971, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1006, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1019, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1587, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0653, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1090, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0941, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1082, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1228, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.0727, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0883, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1369, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0814, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0942, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0890, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2231, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1274, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1316, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1369, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0613, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1650, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1057, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1567, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1745, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1016, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1306, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.2036, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0959, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1664, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1336, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1117, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1001, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1560, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1048, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1078, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1100, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0875, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1134, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1259, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1376, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1140, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0989, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1194, grad_fn=<MseLossBackward0>)
Training loss:

Training loss: tensor(0.0995, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0747, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1961, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1710, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1126, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1709, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1348, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1549, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.0929, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1090, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1301, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1520, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1045, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.2061, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1147, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1167, grad_fn=<MseLossBackward0>)
Training loss: tensor(0.1176, grad_fn=<MseLossBackward0>)
Training loss:

## Predict outputs

In [17]:

for i in range(len(X_test_tr)):
    print("**************************************************")
    print("input")
    print(X_test_tr[i])
    print("preds, real")
    preds = model(X_test_tr[i])

    np_pred = preds.detach().numpy()              ## [0]
    np_real = y_test_tr[i].detach().numpy()


    for j in range(len(np_pred)):
        print((np_pred[j], np_real[j]))
    



**************************************************
input
tensor([-0.6746, -0.4502, -0.5039, -1.3071,  0.0000,  0.0000,  0.0000,  0.0000,
         0.0000, -1.7780])
preds, real
(-0.46002662, -0.39696112)
(1.1710917, 1.2066705)
(-0.31973016, -0.12531227)
(-0.94827056, -0.75444394)
(-0.913869, -0.75592893)
(-0.97501653, -0.75426406)
(0.13841298, 0.015406219)
(-0.05245635, 0.019047316)
(0.14797057, 0.1761152)
(-1.8454828, -1.1784332)
(0.4707379, 0.5987946)
(0.3194221, 0.401798)
(0.22359324, 1.4128103)
(-1.1378942, -0.80931795)
(-0.74922323, -0.631744)
(-0.44249845, -0.556402)
(1.9950607, 1.816122)
**************************************************
input
tensor([-0.6746, -0.4502,  2.6633, -1.3071,  0.0000,  0.0000,  0.0000,  0.0000,
         0.0000, -1.7780])
preds, real
(-0.4270332, -0.34652972)
(0.88221717, 1.3610646)
(0.06905574, -0.08125172)
(-0.63133097, -0.75444394)
(-0.61943686, -0.75592893)
(-0.62703097, -0.75426406)
(0.6892816, 1.020035)
(0.21983907, 0.3497931)
(-0.18603681, -0.374

In [18]:

preds = model(X_test_tr)
print('Test loss:', loss_fn(     preds,                   y_test_tr          ))
print('Testing R**2:', r2_score( preds.detach().numpy(),  y_test_tr.numpy()  ))


Test loss: tensor(0.2373, grad_fn=<MseLossBackward0>)
Testing R**2: 0.6153083986843413


In [19]:

'''

model.eval()

dummy_input = torch.randn(1, 10)


input_names = ["input1"]
output_names = ["output1", "output2"]

torch.onnx.export(
  model, 
  dummy_input, 
  "ONNXmodels/CFDallNORM.onnx", 
  verbose=False, 
  input_names  = input_names,
  output_names = output_names
)

'''


'\n\nmodel.eval()\n\ndummy_input = torch.randn(1, 10)\n\n\ninput_names = ["input1"]\noutput_names = ["output1", "output2"]\n\ntorch.onnx.export(\n  model, \n  dummy_input, \n  "ONNXmodels/CFDallNORM.onnx", \n  verbose=False, \n  input_names  = input_names,\n  output_names = output_names\n)\n\n'